In [1]:
%load_ext autoreload
%autoreload 2

import wandb

api = wandb.Api()
filters = {"tags": "all_frames_aggregation"}
runs = list(api.runs("romeu/diffusion-3D-features", filters=filters))
print(len(runs))

8


In [8]:
from omegaconf import OmegaConf
from scripts.run_generative_rendering import RunGenerativeRenderingConfig
from text3d2video.evaluation.video_comparison import scene_key_fun
from text3d2video.util import group_list_by

def group_fun(run):
    config: RunGenerativeRenderingConfig = OmegaConf.create(run.config)
    return config.generative_rendering.aggregate_all_frames

runs_grouped = group_list_by(runs, group_fun)

def run_num_keyframes(run):
    config: RunGenerativeRenderingConfig = OmegaConf.create(run.config)
    return config.generative_rendering.num_pre_attn_keyframes

for group in runs_grouped:
    group.sort(key=run_num_keyframes)

In [14]:
from text3d2video.evaluation.video_comparison import VideoLabel, make_comparison_vid


def info_fun(run, _):
    label = VideoLabel()
    config: RunGenerativeRenderingConfig = OmegaConf.create(run.config)

    n_pre_attn_kf = config.generative_rendering.num_pre_attn_keyframes
    all_frames_aggregation = config.generative_rendering.aggregate_all_frames

    label.content = (
        f"num_pre_att keyframes: {n_pre_attn_kf}\n"
        + f"aggregate_only_on_keyframes: {not all_frames_aggregation}"
    )
    return label


make_comparison_vid(
    runs_grouped,
    info_fun_top=info_fun,
    title="Aggregating over all frames",
    download=False,
).ipython_display()

Moviepy - Building video __temp__.mp4.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4
